In [ ]:
# imageFiltering-GaussianPyramid

import matplotlib.pyplot as plt
import numpy as np
from scipy.signal import sepfir2d

im = plt.imread( 'mandrill.png' ) # load image
h = [1/16,4/16,6/16,4/16,1/16]; # blur filter
N = 3 # number of pyramid levels

P = []
P.append(im) # first pyramid level
for k in range(1,N): # build pyramid
    im2 = np.zeros( im.shape )
    for z in range(3):
        im2[:,:,z] = sepfir2d( im[:,:,z], h, h ) # blur each color channel
    im2 = im2[0:-1:2,0:-1:2,:]
    P.append(im2) # down-sample
    im = im2

# display pyramid  
fig, ax = plt.subplots(nrows=1, ncols=N, figsize=(15, 7), dpi=72, sharex=True, sharey=True)
for k in range(N-1,-1,-1):
    ax[k].imshow(P[k])

In [ ]:
# imageFiltering-LaplacianPyramid

import matplotlib.pyplot as plt
import numpy as np
import cv2
from scipy.signal import sepfir2d

im = plt.imread( 'mandrill.png' ) # load image
h = [1/16,4/16,6/16,4/16,1/16]; # blur filter
N = 4 # number of pyramid levels

# Gaussian pyramid
G = []
G.append(im) # first pyramid level
for k in range(1,N): # pyramid levels
    im2 = np.zeros( im.shape )
    for z in range(3):
        im2[:,:,z] = sepfir2d( im[:,:,z], h, h ) # blur each color channel
    im2 = im2[0:-1:2, 0:-1:2,:] # down-sample
    im = im2
    G.append(im2)

#  Laplacian pyramid
L = []
for k in range(0,N-1): # pyramid levels
    l1 = G[k]
    l2 = G[k+1]
    l2 = cv2.resize(l2, (0,0), fx=2, fy=2) # up-sample
    D  = l1 - l2
    D  = D - np.min(D) # scale in [0,1]
    D  = D / np.max(D) # for display purposes
    L.append(D)
L.append(G[N-1])
    
# display pyramid  
fig, ax = plt.subplots(nrows=1, ncols=N, figsize=(15, 7), dpi=72, sharex=True, sharey=True)
for k in range(N-1,-1,-1):
    ax[k].imshow(L[k])

In [ ]:
# imageFiltering-edges

import numpy as np
import matplotlib.pyplot as plt
import math
from scipy.signal import sepfir2d
from IPython.display import clear_output
from time import sleep

# compute space-time derivatives
img = plt.imread( "disc.png" )
p  = [0.030320, 0.249724, 0.439911, 0.249724, 0.030320]
d  = [-0.104550, -0.292315, 0.0, 0.292315, 0.104550]

img_x  = sepfir2d( img, d, p ) # spatial (x) derivative
img_y  = sepfir2d( img, p, d ) # spatial (y) derivative

for th in range(0,361,5):
    plt.figure(figsize=(10,10))
    plt.imshow( np.cos(np.radians(th))*img_x + np.sin(np.radians(th))*img_y, cmap='gray')
    plt.title( th )
    plt.show()
    sleep(0.1)
    clear_output(wait=True)

In [ ]:
# imageFiltering-features

import matplotlib.pyplot as plt
from skimage.feature import hog
from skimage import data, exposure

im = plt.imread( "al.jpg" )
fd, hog_image = hog(im, orientations=8, pixels_per_cell=(16, 16),
                    cells_per_block=(1, 1), visualize=True, 
                    multichannel=False)
hog_image_rescaled = exposure.rescale_intensity(hog_image, in_range=(0, 10))

plt.figure(figsize=(20,10))
plt.subplot(1,2,1)
plt.imshow(im, cmap='gray')
plt.subplot(1,2,2)
plt.imshow(hog_image_rescaled, cmap='gray')